### Imports

In [1]:
import numpy as np
import keras
import os
import tensorflow as tf
from keras.layers import LSTM, Dense, Input
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from tqdm import tqdm

os.environ["CUDA_VISIBLE_DEVICES"] = "0"
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'

### Check GPU

In [2]:
physical_devices = tf.config.experimental.list_physical_devices('GPU')
print("Num GPUs Available: ", len(physical_devices))

Num GPUs Available:  1


In [3]:
print(tf.config.list_physical_devices('GPU'))

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


### Define the model parameters

In [4]:
batch_size = 16
epochs = 50
latent_dim = 256
num_samples = 40000
data_path = "pol-eng/pol.txt"

### Read the data

In [5]:
input_texts = []
target_texts = []
input_characters = set()
target_characters = set()
with open(data_path, "r", encoding="utf-8") as f:
    lines = f.read().split("\n")
for line in lines[: min(num_samples, len(lines) - 1)]:
    input_text, target_text, _ = line.split("\t")

    target_text = "\t" + target_text + "\n"
    input_texts.append(input_text)
    target_texts.append(target_text)
    for char in input_text:
        if char not in input_characters:
            input_characters.add(char)
    for char in target_text:
        if char not in target_characters:
            target_characters.add(char)

input_characters = sorted(list(input_characters))
target_characters = sorted(list(target_characters))
num_encoder_tokens = len(input_characters)
num_decoder_tokens = len(target_characters)
max_encoder_seq_length = max([len(txt) for txt in input_texts])
max_decoder_seq_length = max([len(txt) for txt in target_texts])

print("Number of samples:", len(input_texts))
print("Number of unique input tokens:", num_encoder_tokens)
print("Number of unique output tokens:", num_decoder_tokens)
print("Max sequence length for inputs:", max_encoder_seq_length)
print("Max sequence length for outputs:", max_decoder_seq_length)

Number of samples: 40000
Number of unique input tokens: 76
Number of unique output tokens: 99
Max sequence length for inputs: 39
Max sequence length for outputs: 68


### Define the input and target data

In [6]:
input_token_index = dict([(char, i) for i, char in enumerate(input_characters)])
target_token_index = dict([(char, i) for i, char in enumerate(target_characters)])

encoder_input_data = np.zeros(
    (len(input_texts), max_encoder_seq_length, num_encoder_tokens),
    dtype="float32",
)
decoder_input_data = np.zeros(
    (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
    dtype="float32",
)
decoder_target_data = np.zeros(
    (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
    dtype="float32",
)

for i, (input_text, target_text) in enumerate(zip(input_texts, target_texts)):
    for t, char in enumerate(input_text):
        encoder_input_data[i, t, input_token_index[char]] = 1.0
    encoder_input_data[i, t + 1 :, input_token_index[" "]] = 1.0
    for t, char in enumerate(target_text):
        decoder_input_data[i, t, target_token_index[char]] = 1.0
        if t > 0:
            decoder_target_data[i, t - 1, target_token_index[char]] = 1.0
    decoder_input_data[i, t + 1 :, target_token_index[" "]] = 1.0
    decoder_target_data[i, t:, target_token_index[" "]] = 1.0

### Define the model

In [7]:
encoder_inputs = Input(shape=(None, num_encoder_tokens))
encoder = LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)

encoder_states = [state_h, state_c]

decoder_inputs = Input(shape=(None, num_decoder_tokens))
decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs, initial_state=encoder_states)
decoder_dense = Dense(num_decoder_tokens, activation="softmax")
decoder_outputs = decoder_dense(decoder_outputs)

### Train the model

In [0]:
model = keras.Model([encoder_inputs, decoder_inputs], decoder_outputs)
model.compile(optimizer="rmsprop", loss="categorical_crossentropy", metrics=["accuracy"])

In [8]:
model.fit(
    [encoder_input_data, decoder_input_data],
    decoder_target_data,
    batch_size=batch_size,
    epochs=epochs,
    validation_split=0.2,
)

model.save("s2s_model.keras")

Epoch 1/50
2000/2000 [==============================] - 46s 19ms/step - loss: 0.7914 - accuracy: 0.7804 - val_loss: 0.9906 - val_accuracy: 0.7111
Epoch 2/50
2000/2000 [==============================] - 34s 17ms/step - loss: 0.5680 - accuracy: 0.8332 - val_loss: 0.8399 - val_accuracy: 0.7529
Epoch 3/50
2000/2000 [==============================] - 35s 17ms/step - loss: 0.4870 - accuracy: 0.8568 - val_loss: 0.7561 - val_accuracy: 0.7769
Epoch 4/50
2000/2000 [==============================] - 35s 17ms/step - loss: 0.4405 - accuracy: 0.8702 - val_loss: 0.7148 - val_accuracy: 0.7894
Epoch 5/50
2000/2000 [==============================] - 37s 18ms/step - loss: 0.4091 - accuracy: 0.8794 - val_loss: 0.6904 - val_accuracy: 0.7963
Epoch 6/50
2000/2000 [==============================] - 35s 18ms/step - loss: 0.3858 - accuracy: 0.8860 - val_loss: 0.6719 - val_accuracy: 0.8025
Epoch 7/50
2000/2000 [==============================] - 35s 18ms/step - loss: 0.3671 - accuracy: 0.8912 - val_loss: 0.6604 -

### Load model

In [8]:
model = keras.models.load_model("s2s_model.keras")

### Encoder model

In [9]:
encoder_inputs = model.input[0]
encoder_outputs, state_h_enc, state_c_enc = model.layers[2].output
encoder_states = [state_h_enc, state_c_enc]
encoder_model = keras.Model(encoder_inputs, encoder_states)

### Decoder model

In [10]:
decoder_inputs = model.input[1]
decoder_state_input_h = keras.Input(shape=(latent_dim,))
decoder_state_input_c = keras.Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
decoder_lstm = model.layers[3]
decoder_outputs, state_h_dec, state_c_dec = decoder_lstm(
    decoder_inputs, initial_state=decoder_states_inputs
)
decoder_states = [state_h_dec, state_c_dec]
decoder_dense = model.layers[4]
decoder_outputs = decoder_dense(decoder_outputs)
decoder_model = keras.Model(
    [decoder_inputs] + decoder_states_inputs, [decoder_outputs] + decoder_states
)

### Define the decoding sequence

In [14]:
reverse_input_char_index = dict((i, char) for char, i in input_token_index.items())
reverse_target_char_index = dict((i, char) for char, i in target_token_index.items())


def decode_sequence(input_seq):
    states_value = encoder_model.predict(input_seq, verbose=0)

    target_seq = np.zeros((1, 1, num_decoder_tokens))
    target_seq[0, 0, target_token_index["\t"]] = 1.0

    stop_condition = False
    decoded_sentence = ""
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict(
            [target_seq] + states_value, verbose=0
        )

        sampled_token_index = np.argmax(output_tokens[0, -1, :])
        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += sampled_char

        if sampled_char == "\n" or len(decoded_sentence) > max_decoder_seq_length:
            stop_condition = True

        target_seq = np.zeros((1, 1, num_decoder_tokens))
        target_seq[0, 0, sampled_token_index] = 1.0

        states_value = [h, c]
    return decoded_sentence

### Sample predictions

In [12]:
for seq_index in range(20):
    input_seq = encoder_input_data[seq_index : seq_index + 1]
    decoded_sentence = decode_sequence(input_seq)
    print("-")
    print("Input sentence:", input_texts[seq_index])
    print("Decoded sentence:", decoded_sentence)

-
Input sentence: Go.
Decoded sentence: Idź się.

-
Input sentence: Hi.
Decoded sentence: Cześć.

-
Input sentence: Run!
Decoded sentence: Uciekaj!

-
Input sentence: Run.
Decoded sentence: Biegnij.

-
Input sentence: Run.
Decoded sentence: Biegnij.

-
Input sentence: Who?
Decoded sentence: Kto?

-
Input sentence: Wow!
Decoded sentence: Jak sprawdzi!

-
Input sentence: Wow!
Decoded sentence: Jak sprawdzi!

-
Input sentence: Duck!
Decoded sentence: Unik!

-
Input sentence: Fire!
Decoded sentence: Staktowa!

-
Input sentence: Fire!
Decoded sentence: Staktowa!

-
Input sentence: Fire!
Decoded sentence: Staktowa!

-
Input sentence: Help!
Decoded sentence: Pomocy!

-
Input sentence: Hide.
Decoded sentence: Utekty to.

-
Input sentence: Jump!
Decoded sentence: Samujesz!

-
Input sentence: Jump.
Decoded sentence: Skok.

-
Input sentence: Stay.
Decoded sentence: Zostań.

-
Input sentence: Stop!
Decoded sentence: Zaczej się!

-
Input sentence: Stop!
Decoded sentence: Zaczej się!

-
Input senten

### Compute BLEU score

In [15]:
def preprocess_text(text):
    return text.strip().split()

def compute_bleu_score(target_texts, range_limit=1000):
    candidate_corpus = []
    references_corpus = []

    for seq_index in tqdm(range(range_limit), desc="Calculating BLEU scores"):
        input_seq = encoder_input_data[seq_index : seq_index + 1]
        decoded_sentence = decode_sequence(input_seq)
        candidate_corpus.append(preprocess_text(decoded_sentence))
        references_corpus.append([preprocess_text(target_texts[seq_index])])

    smoothie = SmoothingFunction().method4
    bleu_scores = [sentence_bleu(ref, cand, smoothing_function=smoothie) for ref, cand in zip(references_corpus, candidate_corpus)]
    average_bleu = sum(bleu_scores) / len(bleu_scores)

    print("BLEU score:", average_bleu)


In [16]:
compute_bleu_score(target_texts, 100)

Calculating BLEU scores: 100%|██████████| 100/100 [01:12<00:00,  1.39it/s]

BLEU score: 0.2236331802292942


In [17]:
compute_bleu_score(target_texts, 1000)

Calculating BLEU scores: 100%|██████████| 1000/1000 [14:39<00:00,  1.14it/s]

BLEU score: 0.152040789734918


In [19]:
compute_bleu_score(target_texts, 10000)

Calculating BLEU scores:   8%|▊         | 761/10000 [13:31<2:44:18,  1.07s/it]


KeyboardInterrupt: 

Patrząc na czas wykonywania się poszczególnych kroków, uczenie modelu przez kilka godzin, blue dla wszystkich elementów powyżej 8 godzin bez rezultatów, porzuciłem dalsze próby i przeszedłem na rozwiązanie na pyTorch, które wykonało się diametralnie szybciej (oba na cuda)